# Optuna Convolutional Neural Net (FCNN)

In [2]:
import numpy as np
import torch
import torch.nn as nn
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import train_test_split
import random
from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader
import torch.optim as optim
import torch.nn.functional as F
import optuna
import time

In [3]:
# load training data
Xtr_loadpath = 'Xtr.csv'
Xts_loadpath = 'Xts.csv'
ytr_loadpath = 'ytr.csv'

Xtr = np.loadtxt(Xtr_loadpath, delimiter=",")
Xts = np.loadtxt(Xts_loadpath, delimiter=",")
ytr = np.loadtxt(ytr_loadpath, delimiter=",")

### Standardizing the Data 

In [4]:
# The model was tested with both standardization, and normalization. Normalization doesn't seem to 
# give good results, that's why we finalized our design with standardization. 
# standardize the training data
from sklearn.preprocessing import StandardScaler
scale= StandardScaler()

Xtr_standardized = scale.fit_transform(Xtr) # revise this line as needed
Xts_standardized = scale.fit_transform(Xts) # revise this line as needed
ytr_standardized = ytr # revise this line as needed

Xtr_torch = torch.Tensor(Xtr_standardized)
Xts_torch = torch.Tensor(Xts_standardized)
ytr_torch = torch.Tensor(ytr_standardized)

# save the standardized training data
Xtr_savepath = 'Xtr_pytorch.csv'
Xts_savepath = 'Xts_pytorch.csv'
ytr_savepath = 'ytr_pytorch.csv'
yts_hat_savepath = 'yts_hat_pytorch.csv'

np.savetxt(Xtr_savepath, Xtr_standardized, delimiter=",")
np.savetxt(Xts_savepath, Xts_standardized, delimiter=",")
np.savetxt(ytr_savepath, ytr_standardized, delimiter=",")


### Train Test Split, and Creation of Pytorch Dataloaders 

In [13]:
x_train,x_test,y_train,y_test = train_test_split(Xtr_torch,ytr_torch,test_size=0.2,random_state = 42)
x_train = x_train.reshape(x_train.shape[0],x_train.shape[1],1).permute(0,2,1)
y_train = y_train.reshape(y_train.shape[0],1,1)
x_test = x_test.reshape(x_test.shape[0],x_test.shape[1],1).permute(0,2,1)
y_test = y_test.reshape(y_test.shape[0],1,1)

train_ds = TensorDataset(x_train, y_train)
test_ds =  TensorDataset(x_test, y_test)
batch_size = 100
train_dl = DataLoader(train_ds, batch_size=batch_size, shuffle=True)
test_dl = DataLoader(test_ds, batch_size=batch_size, shuffle=True)

### Training the model 

In [9]:
def training_model(model, optimizer, train_dl, test_dl, num_epoch, trial,verbose=True):
    
    opt = optimizer
    criterion = nn.BCELoss()
    
    a_tr_loss = np.zeros([num_epoch])
    a_tr_accuracy = np.zeros([num_epoch])
    a_ts_loss = np.zeros([num_epoch])
    a_ts_accuracy = np.zeros([num_epoch])

    for epoch in range(num_epoch):
        correct = 0 # initialize error counter
        total = 0 # initialize total counter
        batch_loss = []
        tic = time.time()

        model.train() # put model in training mode
        # iterate over training set
        for train_iter, data in enumerate(train_dl):
            x_batch,y_batch = data
            y_batch = y_batch.view(-1,1)
            out = model(x_batch)
            # Compute Loss
            loss = criterion(out.clamp(0,1),y_batch.type(torch.float))
            batch_loss.append(loss.item())
            # Zero gradients
            opt.zero_grad()
            # Compute gradients using back propagation
            loss.backward()
            # Take an optimization 'step'
            opt.step()
            predicted = out.clamp(0,1).round().type(torch.long)
            total += y_batch.size(0)
            correct += (predicted == y_batch).sum().item()

        a_tr_loss[epoch] = np.mean(batch_loss) # Compute average loss over epoch
        a_tr_accuracy[epoch] = 100*correct/total

        correct = 0
        total = 0
        batch_loss = []
        model.eval() # put model in evaluation mode
        with torch.no_grad():
            for data in test_dl:
                images, labels = data
                labels = labels.view(-1,1)
                out = model(images)
                batch_loss.append(criterion(out.clamp(0,1),labels.type(torch.float)).item())
                predicted = out.clamp(0,1).round().type(torch.long)
                total += labels.size(0)
                correct += (predicted == labels).sum().item()

        a_ts_loss[epoch] = np.mean(batch_loss)
        a_ts_accuracy[epoch] = 100*correct/total
        elapsed = time.time()-tic
    
        # Print details every print_mod epoch
        if(verbose):
            print('Epoch: {0:2d}   Train Loss: {1:.3f}   '.format(epoch+1, a_tr_loss[epoch])
              +'Train Accuracy: {0:.2f}    Test Loss: {1:.3f}   '.format(a_tr_accuracy[epoch], a_ts_loss[epoch])
              +'Test Accuracy: {0:.2f}   '.format(a_ts_accuracy[epoch])
              +'Time: {0:.2f}sec'.format(elapsed))
            
        # Handle pruning based on the intermediate value.
        
        trial.report(a_ts_accuracy[epoch], epoch)
        if trial.should_prune():
            raise optuna.exceptions.TrialPruned()
    
    return (sum(a_ts_accuracy[190:200])/10)
            


### Defining the model 

In [17]:
def define_model(trial):
    
    conv_layers = trial.suggest_int("conv_layers", 2, 5)
    conv_kernel= trial.suggest_int("conv_kernel", 3, 5, step=2)
    activation = trial.suggest_categorical("activation", ["ReLU","ELU","LeakyReLU"])
    batch_norm = trial.suggest_categorical("batch_norm", ["With_BN","Without_BN"])
    pooling= trial.suggest_categorical("pooling", ["Max_Pooling", "Avg_Pooling"])
    pool_kernel=trial.suggest_int("pool_kernel", 1, 2)
    layers = []
    p = trial.suggest_float("dropout", 0, 0.5)
    in_channels = 1
    in_features=8
    for i in range(conv_layers):
        out_channels = trial.suggest_int("n_units_l{}".format(i), 16, 64,step=16)
        layers.append(nn.Conv1d(in_channels, out_channels,conv_kernel,padding='same'))
        if batch_norm == "With_BN":
            layers.append(nn.BatchNorm1d(out_channels))
        if activation == "ReLU":
            layers.append(nn.ReLU())
        if activation == "ELU":
            layers.append(nn.ELU()) 
        if activation == "LeakyReLU":
            layers.append(nn.LeakyReLU()) 
        if pooling == "Max_Pooling":
            layers.append(nn.MaxPool1d(pool_kernel, stride=None,ceil_mode=True))
            out_features= np.ceil(1+ (in_features -pool_kernel)/pool_kernel)
            in_features=out_features
        if pooling == "Avg_Pooling":
            layers.append(nn.AvgPool1d(pool_kernel, stride=None,ceil_mode=True))
            out_features= np.ceil(1+ (in_features-pool_kernel)/pool_kernel)
            in_features=out_features
        layers.append(nn.Dropout(p))
        in_channels= out_channels
        
    layers.append(nn.Flatten())
    layers.append(nn.Linear(int(in_channels*in_features),1))   
    
    return nn.Sequential(*layers)

### Defining Objective Function 

In [18]:
def objective(trial):
    
    num_epoch=200
    Xtr_standardized = scale.fit_transform(Xtr) # revise this line as needed
    Xts_standardized = scale.fit_transform(Xts) # revise this line as needed
    ytr_standardized = ytr # revise this line as needed
    Xtr_torch = torch.Tensor(Xtr_standardized)
    Xts_torch = torch.Tensor(Xts_standardized)
    ytr_torch = torch.Tensor(ytr_standardized)

    x_train,x_test,y_train,y_test = train_test_split(Xtr_torch,ytr_torch,test_size=0.2,random_state = 42)
    x_train = x_train.reshape(x_train.shape[0],x_train.shape[1],1).permute(0,2,1)
    y_train = y_train.reshape(y_train.shape[0],1,1)
    x_test = x_test.reshape(x_test.shape[0],x_test.shape[1],1).permute(0,2,1)
    y_test = y_test.reshape(y_test.shape[0],1,1)

    train_ds = TensorDataset(x_train, y_train)
    test_ds =  TensorDataset(x_test, y_test)
    batch_size = 100
    train_dl = DataLoader(train_ds, batch_size=batch_size, shuffle=True)
    test_dl = DataLoader(test_ds, batch_size=batch_size, shuffle=True)
    
    model = define_model(trial)
    optimizer_name = trial.suggest_categorical("optimizer", ["Adam", "RMSprop", "SGD"])
    lr = trial.suggest_loguniform("lr", 1e-4, 1e-2) #
    optimizer = getattr(optim, optimizer_name)(model.parameters(), lr=lr)
    accuracy = training_model(model,optimizer, train_dl, test_dl,num_epoch,verbose=True,trial=trial)
    
    return accuracy
    


### Creating an optuna study 

In [19]:
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=1000, timeout=None)

[I 2022-12-08 11:52:54,949] A new study created in memory with name: no-name-88a24a09-67fa-4ab4-b14e-b07f1dd479a2
C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_11184\3967207748.py:25: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-4, 1e-2) #


Epoch:  1   Train Loss: 6.182   Train Accuracy: 63.56    Test Loss: 1.595   Test Accuracy: 72.85   Time: 0.49sec
Epoch:  2   Train Loss: 15.677   Train Accuracy: 65.88    Test Loss: 10.175   Test Accuracy: 64.25   Time: 0.43sec
Epoch:  3   Train Loss: 11.687   Train Accuracy: 66.46    Test Loss: 10.454   Test Accuracy: 69.50   Time: 0.45sec
Epoch:  4   Train Loss: 11.276   Train Accuracy: 70.70    Test Loss: 6.102   Test Accuracy: 68.55   Time: 0.65sec
Epoch:  5   Train Loss: 9.243   Train Accuracy: 69.69    Test Loss: 8.715   Test Accuracy: 69.75   Time: 0.47sec
Epoch:  6   Train Loss: 7.265   Train Accuracy: 68.38    Test Loss: 2.635   Test Accuracy: 67.85   Time: 0.51sec
Epoch:  7   Train Loss: 8.260   Train Accuracy: 67.45    Test Loss: 15.964   Test Accuracy: 58.45   Time: 0.61sec
Epoch:  8   Train Loss: 7.903   Train Accuracy: 69.61    Test Loss: 3.213   Test Accuracy: 75.25   Time: 0.54sec
Epoch:  9   Train Loss: 5.730   Train Accuracy: 72.35    Test Loss: 2.185   Test Accuracy:

Epoch: 73   Train Loss: 24.270   Train Accuracy: 74.67    Test Loss: 25.419   Test Accuracy: 73.50   Time: 0.60sec
Epoch: 74   Train Loss: 24.576   Train Accuracy: 74.17    Test Loss: 24.830   Test Accuracy: 73.95   Time: 0.41sec
Epoch: 75   Train Loss: 24.249   Train Accuracy: 74.61    Test Loss: 24.926   Test Accuracy: 73.50   Time: 0.44sec
Epoch: 76   Train Loss: 23.591   Train Accuracy: 75.06    Test Loss: 23.524   Test Accuracy: 75.50   Time: 0.44sec
Epoch: 77   Train Loss: 23.695   Train Accuracy: 75.24    Test Loss: 23.820   Test Accuracy: 75.05   Time: 0.42sec
Epoch: 78   Train Loss: 23.428   Train Accuracy: 75.20    Test Loss: 22.588   Test Accuracy: 75.75   Time: 0.39sec
Epoch: 79   Train Loss: 24.074   Train Accuracy: 74.09    Test Loss: 22.483   Test Accuracy: 75.60   Time: 0.48sec
Epoch: 80   Train Loss: 24.466   Train Accuracy: 73.51    Test Loss: 22.931   Test Accuracy: 75.55   Time: 0.57sec
Epoch: 81   Train Loss: 24.385   Train Accuracy: 73.72    Test Loss: 22.489   Te

Epoch: 144   Train Loss: 20.847   Train Accuracy: 76.88    Test Loss: 18.994   Test Accuracy: 79.00   Time: 0.46sec
Epoch: 145   Train Loss: 20.038   Train Accuracy: 77.58    Test Loss: 19.067   Test Accuracy: 78.05   Time: 0.44sec
Epoch: 146   Train Loss: 20.938   Train Accuracy: 76.69    Test Loss: 19.097   Test Accuracy: 78.95   Time: 0.64sec
Epoch: 147   Train Loss: 20.334   Train Accuracy: 77.41    Test Loss: 19.107   Test Accuracy: 77.85   Time: 0.50sec
Epoch: 148   Train Loss: 20.347   Train Accuracy: 76.95    Test Loss: 19.306   Test Accuracy: 78.05   Time: 0.47sec
Epoch: 149   Train Loss: 21.419   Train Accuracy: 75.88    Test Loss: 17.865   Test Accuracy: 78.80   Time: 0.49sec
Epoch: 150   Train Loss: 20.488   Train Accuracy: 76.94    Test Loss: 19.731   Test Accuracy: 78.65   Time: 0.55sec
Epoch: 151   Train Loss: 20.288   Train Accuracy: 77.79    Test Loss: 18.954   Test Accuracy: 78.50   Time: 0.47sec
Epoch: 152   Train Loss: 20.876   Train Accuracy: 77.34    Test Loss: 21

[I 2022-12-08 11:54:33,147] Trial 0 finished with value: 75.44999999999999 and parameters: {'conv_layers': 2, 'conv_kernel': 3, 'activation': 'ReLU', 'batch_norm': 'With_BN', 'pooling': 'Avg_Pooling', 'pool_kernel': 2, 'dropout': 0.3556070988507522, 'n_units_l0': 32, 'n_units_l1': 64, 'optimizer': 'Adam', 'lr': 0.007953621592281593}. Best is trial 0 with value: 75.44999999999999.


...

Epoch:  1   Train Loss: 1.675   Train Accuracy: 65.55    Test Loss: 0.817   Test Accuracy: 77.95   Time: 0.70sec


C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_11184\3967207748.py:25: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-4, 1e-2) #
[I 2022-12-08 18:27:19,076] Trial 998 pruned. 


Epoch:  1   Train Loss: 1.059   Train Accuracy: 74.79    Test Loss: 0.582   Test Accuracy: 80.50   Time: 0.66sec


C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_11184\3967207748.py:25: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-4, 1e-2) #
[I 2022-12-08 18:27:19,990] Trial 999 pruned. 


Epoch:  1   Train Loss: 0.831   Train Accuracy: 72.26    Test Loss: 0.738   Test Accuracy: 79.00   Time: 0.70sec


In [20]:
best_trial = study.best_trial

for key, value in best_trial.params.items():
    print("{}: {}".format(key, value))
print("Accuracy:",study.best_value)

conv_layers: 3
conv_kernel: 5
activation: LeakyReLU
batch_norm: Without_BN
pooling: Avg_Pooling
pool_kernel: 1
dropout: 0.08110457293601621
n_units_l0: 48
n_units_l1: 16
n_units_l2: 48
optimizer: RMSprop
lr: 0.0006645887720724897
Accuracy: 84.89


In [29]:
# EPOCHS= 500
# BATCHSIZE = 100
# study = optuna.create_study(study_name='study_1000_trials_1',storage='sqlite:///study_1000_trials_1.db',
#                             pruner=optuna.pruners.MedianPruner(n_startup_trials=20, n_warmup_steps=50, 
#                                                                interval_steps=10,n_min_trials=10),direction="maximize", 
#                             sampler=optuna.samplers.TPESampler(),load_if_exists=True)
study = optuna.create_study(direction="maximize")
study.optimize(objective, n_trials=1000, timeout=None)

[I 2022-12-07 16:47:52,941] A new study created in memory with name: no-name-5971ccaa-8084-4c20-be5a-b35cc9facfa4
C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_24852\3040680903.py:20: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-6, 1e-1) #


Epoch:  1   Train Loss: 0.645   Train Accuracy: 65.03    Test Loss: 0.642   Test Accuracy: 64.40   Time: 0.54sec
Epoch:  2   Train Loss: 0.641   Train Accuracy: 65.08    Test Loss: 0.636   Test Accuracy: 64.40   Time: 0.68sec
Epoch:  3   Train Loss: 0.635   Train Accuracy: 65.14    Test Loss: 0.631   Test Accuracy: 64.40   Time: 0.60sec
Epoch:  4   Train Loss: 0.633   Train Accuracy: 65.14    Test Loss: 0.621   Test Accuracy: 64.40   Time: 0.55sec
Epoch:  5   Train Loss: 0.626   Train Accuracy: 65.45    Test Loss: 0.614   Test Accuracy: 64.40   Time: 0.59sec
Epoch:  6   Train Loss: 0.620   Train Accuracy: 66.16    Test Loss: 0.602   Test Accuracy: 66.75   Time: 0.51sec
Epoch:  7   Train Loss: 0.612   Train Accuracy: 67.04    Test Loss: 0.590   Test Accuracy: 67.35   Time: 0.47sec
Epoch:  8   Train Loss: 0.608   Train Accuracy: 67.94    Test Loss: 0.579   Test Accuracy: 68.15   Time: 0.59sec
Epoch:  9   Train Loss: 0.600   Train Accuracy: 69.03    Test Loss: 0.564   Test Accuracy: 71.65

Epoch: 74   Train Loss: 0.513   Train Accuracy: 77.12    Test Loss: 0.485   Test Accuracy: 79.25   Time: 0.50sec
Epoch: 75   Train Loss: 0.511   Train Accuracy: 77.15    Test Loss: 0.486   Test Accuracy: 79.20   Time: 0.56sec
Epoch: 76   Train Loss: 0.512   Train Accuracy: 77.39    Test Loss: 0.484   Test Accuracy: 79.10   Time: 0.57sec
Epoch: 77   Train Loss: 0.517   Train Accuracy: 76.84    Test Loss: 0.485   Test Accuracy: 78.90   Time: 0.75sec
Epoch: 78   Train Loss: 0.512   Train Accuracy: 77.08    Test Loss: 0.487   Test Accuracy: 79.35   Time: 0.58sec
Epoch: 79   Train Loss: 0.517   Train Accuracy: 76.61    Test Loss: 0.488   Test Accuracy: 79.35   Time: 0.56sec
Epoch: 80   Train Loss: 0.517   Train Accuracy: 76.95    Test Loss: 0.485   Test Accuracy: 79.35   Time: 0.49sec
Epoch: 81   Train Loss: 0.510   Train Accuracy: 77.35    Test Loss: 0.485   Test Accuracy: 79.40   Time: 0.55sec
Epoch: 82   Train Loss: 0.506   Train Accuracy: 77.50    Test Loss: 0.487   Test Accuracy: 79.30

Epoch: 147   Train Loss: 0.506   Train Accuracy: 77.59    Test Loss: 0.486   Test Accuracy: 79.45   Time: 0.69sec
Epoch: 148   Train Loss: 0.503   Train Accuracy: 77.72    Test Loss: 0.485   Test Accuracy: 79.45   Time: 0.56sec
Epoch: 149   Train Loss: 0.507   Train Accuracy: 77.60    Test Loss: 0.484   Test Accuracy: 79.35   Time: 0.48sec
Epoch: 150   Train Loss: 0.501   Train Accuracy: 77.60    Test Loss: 0.485   Test Accuracy: 79.30   Time: 0.55sec
Epoch: 151   Train Loss: 0.501   Train Accuracy: 77.76    Test Loss: 0.486   Test Accuracy: 78.90   Time: 0.52sec
Epoch: 152   Train Loss: 0.507   Train Accuracy: 77.12    Test Loss: 0.484   Test Accuracy: 79.40   Time: 0.52sec
Epoch: 153   Train Loss: 0.494   Train Accuracy: 77.81    Test Loss: 0.484   Test Accuracy: 79.35   Time: 0.72sec
Epoch: 154   Train Loss: 0.505   Train Accuracy: 77.45    Test Loss: 0.484   Test Accuracy: 79.40   Time: 0.55sec
Epoch: 155   Train Loss: 0.504   Train Accuracy: 77.46    Test Loss: 0.485   Test Accura

[I 2022-12-07 16:49:43,905] Trial 0 finished with value: 79.15 and parameters: {'n_layers': 3, 'activation': 'Sigmoid', 'batch_norm': 'Yes', 'n_units_l0': 49, 'dropout_0': 0.49508185357073287, 'n_units_l1': 94, 'dropout_1': 0.4060258654066278, 'n_units_l2': 114, 'dropout_2': 0.020060947518677985, 'optimizer': 'SGD', 'lr': 0.008273089284567384}. Best is trial 0 with value: 79.15.


...

Epoch:  2   Train Loss: 0.410   Train Accuracy: 82.78    Test Loss: 0.358   Test Accuracy: 84.35   Time: 1.12sec


C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_24852\3040680903.py:20: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-6, 1e-1) #
[I 2022-12-07 20:23:26,130] Trial 998 pruned. 


Epoch:  1   Train Loss: 0.485   Train Accuracy: 77.78    Test Loss: 0.425   Test Accuracy: 80.90   Time: 1.34sec


C:\Users\Hassan Iftikhar\AppData\Local\Temp\ipykernel_24852\3040680903.py:20: FutureWarning: suggest_loguniform has been deprecated in v3.0.0. This feature will be removed in v6.0.0. See https://github.com/optuna/optuna/releases/tag/v3.0.0. Use :func:`~optuna.trial.Trial.suggest_float` instead.
  lr = trial.suggest_loguniform("lr", 1e-6, 1e-1) #
[I 2022-12-07 20:23:27,658] Trial 999 pruned. 


Epoch:  1   Train Loss: 0.472   Train Accuracy: 78.64    Test Loss: 0.402   Test Accuracy: 82.90   Time: 1.33sec


In [30]:
best_trial = study.best_trial

for key, value in best_trial.params.items():
    print("{}: {}".format(key, value))
print("Accuracy:",study.best_value)

n_layers: 2
activation: LeakyReLU
batch_norm: Yes
n_units_l0: 116
dropout_0: 0.09797677421301106
n_units_l1: 50
dropout_1: 0.32808516967402845
optimizer: RMSprop
lr: 0.004059919576147139
Accuracy: 87.65


In [50]:
# TODO
import time

num_epoch = 100

a_tr_loss = np.zeros([num_epoch])
a_tr_accuracy = np.zeros([num_epoch])
a_ts_loss = np.zeros([num_epoch])
a_ts_accuracy = np.zeros([num_epoch])

for epoch in range(num_epoch):
    correct = 0 # initialize error counter
    total = 0 # initialize total counter
    batch_loss = []
    tic = time.time()
    
    model1.train() # put model in training mode
    # iterate over training set
    for train_iter, data in enumerate(train_dl):
        x_batch,y_batch = data
        y_batch = y_batch.view(-1,1)
        out = model1(x_batch)
        # Compute Loss
        loss = criterion(out.clamp(0,1),y_batch.type(torch.float))
        batch_loss.append(loss.item())
        # Zero gradients
        opt.zero_grad()
        # Compute gradients using back propagation
        loss.backward()
        # Take an optimization 'step'
        opt.step()
        predicted = out.clamp(0,1).round().type(torch.long)
        total += y_batch.size(0)
        correct += (predicted == y_batch).sum().item()
        
    a_tr_loss[epoch] = np.mean(batch_loss) # Compute average loss over epoch
    a_tr_accuracy[epoch] = 100*correct/total
    
    correct = 0
    total = 0
    batch_loss = []
    model1.eval() # put model in evaluation mode
    with torch.no_grad():
        for data in test_dl:
            images, labels = data
            labels = labels.view(-1,1)
            out = model1(images)
            batch_loss.append(criterion(out.clamp(0,1),labels.type(torch.float)).item())
            predicted = out.clamp(0,1).round().type(torch.long)
            total += labels.size(0)
            correct += (predicted == labels).sum().item()
            
    a_ts_loss[epoch] = np.mean(batch_loss)
    a_ts_accuracy[epoch] = 100*correct/total
    elapsed = time.time()-tic
    
    # Print details every print_mod epoch
    print('Epoch: {0:2d}   Train Loss: {1:.3f}   '.format(epoch+1, a_tr_loss[epoch])
          +'Train Accuracy: {0:.2f}    Test Loss: {1:.3f}   '.format(a_tr_accuracy[epoch], a_ts_loss[epoch])
          +'Test Accuracy: {0:.2f}   '.format(a_ts_accuracy[epoch])
          +'Time: {0:.2f}sec'.format(elapsed))

Epoch:  1   Train Loss: 0.549   Train Accuracy: 73.15    Test Loss: 0.476   Test Accuracy: 78.05   Time: 0.51sec
Epoch:  2   Train Loss: 0.484   Train Accuracy: 78.74    Test Loss: 0.474   Test Accuracy: 78.35   Time: 0.62sec
Epoch:  3   Train Loss: 0.477   Train Accuracy: 78.85    Test Loss: 0.468   Test Accuracy: 78.05   Time: 0.59sec
Epoch:  4   Train Loss: 0.471   Train Accuracy: 78.85    Test Loss: 0.456   Test Accuracy: 78.55   Time: 0.60sec
Epoch:  5   Train Loss: 0.457   Train Accuracy: 79.11    Test Loss: 0.442   Test Accuracy: 78.70   Time: 0.52sec
Epoch:  6   Train Loss: 0.447   Train Accuracy: 79.83    Test Loss: 0.435   Test Accuracy: 79.60   Time: 0.64sec
Epoch:  7   Train Loss: 0.441   Train Accuracy: 79.97    Test Loss: 0.428   Test Accuracy: 80.25   Time: 0.65sec
Epoch:  8   Train Loss: 0.440   Train Accuracy: 80.31    Test Loss: 0.425   Test Accuracy: 80.65   Time: 0.54sec
Epoch:  9   Train Loss: 0.438   Train Accuracy: 80.29    Test Loss: 0.421   Test Accuracy: 80.90

Epoch: 74   Train Loss: 0.347   Train Accuracy: 85.10    Test Loss: 0.332   Test Accuracy: 86.90   Time: 0.66sec
Epoch: 75   Train Loss: 0.351   Train Accuracy: 85.00    Test Loss: 0.336   Test Accuracy: 86.35   Time: 0.54sec
Epoch: 76   Train Loss: 0.349   Train Accuracy: 85.40    Test Loss: 0.331   Test Accuracy: 86.50   Time: 0.68sec
Epoch: 77   Train Loss: 0.347   Train Accuracy: 85.39    Test Loss: 0.327   Test Accuracy: 86.95   Time: 0.80sec
Epoch: 78   Train Loss: 0.350   Train Accuracy: 84.85    Test Loss: 0.335   Test Accuracy: 86.95   Time: 0.56sec
Epoch: 79   Train Loss: 0.345   Train Accuracy: 85.49    Test Loss: 0.330   Test Accuracy: 87.10   Time: 0.60sec
Epoch: 80   Train Loss: 0.348   Train Accuracy: 84.96    Test Loss: 0.330   Test Accuracy: 86.80   Time: 0.71sec
Epoch: 81   Train Loss: 0.349   Train Accuracy: 84.85    Test Loss: 0.331   Test Accuracy: 87.35   Time: 0.65sec
Epoch: 82   Train Loss: 0.348   Train Accuracy: 85.05    Test Loss: 0.329   Test Accuracy: 87.30

In [51]:
# compute the training accuracy
with torch.no_grad():
    predict = model1(torch.Tensor(Xtr_standardized)).detach().numpy().ravel()
    

auc = roc_auc_score(ytr_standardized,predict)
print('training auc: ',auc)

training auc:  0.9199856429850293


This model when uploaded to Kaggle showed pretty low AUC score 